In [0]:
%pip install emoji
%pip install --upgrade google-generativeai
%pip install azure-core
%pip install azure-ai-textanalytics
%pip install transformers
%pip install torch
%pip install nltk
import nltk
nltk.download("vader_lexicon")

  Obtaining dependency information for emoji from https://files.pythonhosted.org/packages/91/db/a0335710caaa6d0aebdaa65ad4df789c15d89b7babd9a30277838a7d9aac/emoji-2.14.1-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/590.6 kB ? eta -:--:--
   ━━╺━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.7/590.6 kB 1.4 MB/s eta 0:00:01
   ━━━━━━━━━━╺━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 153.6/590.6 kB 2.1 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 590.6/590.6 kB 5.7 MB/s eta 0:00:00
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
  Obtaining dependency information for google-generativeai from https://files.pythonhosted.org/packages/6e/40/c42ff9ded9f09ec9392879a8e6538a00b2dc185e834a3392917626255419/google_generativeai-0.8.5-py3-none-any.whl.metadata
  Obtaining dependency information for google-ai-generativelanguage==0.6.15 from https://files.pythonhosted.org/packages/7c/a3/67b8a6ff5001a1d886492

[nltk_data] Downloading package vader_lexicon to /root/nltk_data...


True

In [0]:
storage_account_name = "" #Your storage account name
container = "" # Your container name
storage_account_key = "" # Your storage account key

In [0]:
dbutils.fs.mount(
    source=f"wasbs://{container}@{storage_account_name}.blob.core.windows.net",
    mount_point="/mnt/yelp",
    extra_configs={f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net": storage_account_key},
)

True

In [0]:
# Path to the file
file_path = "/mnt/yelp/yelp_academic_dataset_review.json"

In [0]:
# Loading data into spark dataframe
df = spark.read.json(file_path)
df.cache()
df.limit(5).display()
df.count()

business_id cool date funny review_id stars text useful user_id XQfwVwDr-v0ZS3_CbbE5Xw 0 2018-07-07 22:09:11 0 KU_O5udG6zpxOg-VcAEodg 3.0 If you decide to eat here, just be aware it is going to take about 2 hours from beginning to end. We have tried it multiple times, because I want to like it! I have been to it's other locations in NJ and never had a bad experience. 

The food is good, but it takes a very long time to come out. The waitstaff is very young, but usually pleasant. We have just had too many experiences where we spent way too long waiting. We usually opt for another diner or restaurant on the weekends, in order to be done quicker. 0 mh_-eMZ6K5RLWhZyISBhwA 7ATYjTIgM3jUlt4UM3IypQ 1 2012-01-03 15:28:18 0 BiTunyQ73aT9WBnpR9DZGw 5.0 I've taken a lot of spin classes over the years, and nothing compares to the classes at Body Cycle. From the nice, clean space and amazing bikes, to the welcoming and motivating instructors, every class is a top notch work out.

For anyone who struggles to fit workouts in, the online scheduling system makes it easy to plan ahead (and there's no need to line up way in advanced like many gyms make you do).

There is no way I can write this review without giving Russell, the owner of Body Cycle, a shout out. Russell's passion for fitness and cycling is so evident, as is his desire for all of his clients to succeed. He is always dropping in to classes to check in/provide encouragement, and is open to ideas and recommendations from anyone. Russell always wears a smile on his face, even when he's kicking your butt in class! 1 OyoGAe7OKpv6SyGZT5g77Q YjUWPpI6HXG530lwP-fb2A 0 2014-02-05 20:30:30 0 saUsX_uimxRlCVr67Z4Jig 3.0 Family diner. Had the buffet. Eclectic assortment: a large chicken leg, fried jalapeño, tamale, two rolled grape leaves, fresh melon. All good. Lots of Mexican choices there. Also has a menu with breakfast served all day long. Friendly, attentive staff. Good place for a casual relaxed meal with no expectations. Next to the Clarion Hotel. 0 8g_iMtfSiwikVnbP2etR0A kxX2SOes4o-D3ZQBkiMRfA 1 2015-01-04 00:01:03 0 AqPFMleE6RsU23_auESxiA 5.0 Wow! Yummy, different, delicious. Our favorite is the lamb curry and korma. With 10 different kinds of naan!!! Don't let the outside deter you (because we almost changed our minds)...go in and try something new! You'll be glad you did! 1 _7bHUi9Uuf5__HHc_Q8guQ e4Vwtrqf-wpJfwesgvdgxQ 1 2017-01-14 20:54:15 0 Sx8TMOWLNuJBWer-0pcmoA 4.0 Cute interior and owner (?) gave us tour of upcoming patio/rooftop area which will be great on beautiful days like today. Cheese curds were very good and very filling. Really like that sandwiches come w salad, esp after eating too many curds! Had the onion, gruyere, tomato sandwich. Wasn't too much cheese which I liked. Needed something else...pepper jelly maybe. Would like to see more menu options added such as salads w fun cheeses. Lots of beer and wine as well as limited cocktails. Next time I will try one of the draft wines. 1 bcjbaE6dDog4jkNY91ncLQ

6990280

In [0]:
%fs ls /mnt/yelp

path name size modificationTime dbfs:/mnt/yelp/yelp_academic_dataset_review.json yelp_academic_dataset_review.json 5341868833 1745106841000

In [0]:
# Creating labels for Sentiment Analysis based on review stars
from pyspark.sql.functions import when

df = df.withColumn(
    "sentiment_based_on_stars",
    when(df.stars >= 4, "POSITIVE")
    .when(df.stars <= 2, "NEGATIVE")
    .otherwise("NEUTRAL")
)
df.limit(5).display()

business_id cool date funny review_id stars text useful user_id sentiment_based_on_stars XQfwVwDr-v0ZS3_CbbE5Xw 0 2018-07-07 22:09:11 0 KU_O5udG6zpxOg-VcAEodg 3.0 If you decide to eat here, just be aware it is going to take about 2 hours from beginning to end. We have tried it multiple times, because I want to like it! I have been to it's other locations in NJ and never had a bad experience. 

The food is good, but it takes a very long time to come out. The waitstaff is very young, but usually pleasant. We have just had too many experiences where we spent way too long waiting. We usually opt for another diner or restaurant on the weekends, in order to be done quicker. 0 mh_-eMZ6K5RLWhZyISBhwA NEUTRAL 7ATYjTIgM3jUlt4UM3IypQ 1 2012-01-03 15:28:18 0 BiTunyQ73aT9WBnpR9DZGw 5.0 I've taken a lot of spin classes over the years, and nothing compares to the classes at Body Cycle. From the nice, clean space and amazing bikes, to the welcoming and motivating instructors, every class is a top notch work out.

For anyone who struggles to fit workouts in, the online scheduling system makes it easy to plan ahead (and there's no need to line up way in advanced like many gyms make you do).

There is no way I can write this review without giving Russell, the owner of Body Cycle, a shout out. Russell's passion for fitness and cycling is so evident, as is his desire for all of his clients to succeed. He is always dropping in to classes to check in/provide encouragement, and is open to ideas and recommendations from anyone. Russell always wears a smile on his face, even when he's kicking your butt in class! 1 OyoGAe7OKpv6SyGZT5g77Q POSITIVE YjUWPpI6HXG530lwP-fb2A 0 2014-02-05 20:30:30 0 saUsX_uimxRlCVr67Z4Jig 3.0 Family diner. Had the buffet. Eclectic assortment: a large chicken leg, fried jalapeño, tamale, two rolled grape leaves, fresh melon. All good. Lots of Mexican choices there. Also has a menu with breakfast served all day long. Friendly, attentive staff. Good place for a casual relaxed meal with no expectations. Next to the Clarion Hotel. 0 8g_iMtfSiwikVnbP2etR0A NEUTRAL kxX2SOes4o-D3ZQBkiMRfA 1 2015-01-04 00:01:03 0 AqPFMleE6RsU23_auESxiA 5.0 Wow! Yummy, different, delicious. Our favorite is the lamb curry and korma. With 10 different kinds of naan!!! Don't let the outside deter you (because we almost changed our minds)...go in and try something new! You'll be glad you did! 1 _7bHUi9Uuf5__HHc_Q8guQ POSITIVE e4Vwtrqf-wpJfwesgvdgxQ 1 2017-01-14 20:54:15 0 Sx8TMOWLNuJBWer-0pcmoA 4.0 Cute interior and owner (?) gave us tour of upcoming patio/rooftop area which will be great on beautiful days like today. Cheese curds were very good and very filling. Really like that sandwiches come w salad, esp after eating too many curds! Had the onion, gruyere, tomato sandwich. Wasn't too much cheese which I liked. Needed something else...pepper jelly maybe. Would like to see more menu options added such as salads w fun cheeses. Lots of beer and wine as well as limited cocktails. Next time I will try one of the draft wines. 1 bcjbaE6dDog4jkNY91ncLQ POSITIVE

Data Preprocessing: I removed the lowercase one since sometimes capitalized words mean something, for axample, “AWFUL” is stronger than “Awful.”

In [0]:
from pyspark.sql.functions import udf
from pyspark.sql.types import StringType
import re
import emoji

def preprocess_text(text):
    if not text:
        return ""
    # Remove URLs
    text = re.sub(r'http\S+|www.\S+', '', text)
    # Remove emojis
    text = emoji.replace_emoji(text, replace='')
    # Remove special characters (keep letters, numbers, punctuation)
    text = re.sub(r"[^a-zA-Z0-9\s.,!?']", ' ', text)
    # Remove extra spaces
    text = re.sub(r'\s+', ' ', text).strip()
    return text

preprocess_text_udf = udf(preprocess_text, StringType())
df = df.withColumn("clean_text", preprocess_text_udf(df["text"]))
df.limit(5).display()

business_id cool date funny review_id stars text useful user_id sentiment_based_on_stars clean_text XQfwVwDr-v0ZS3_CbbE5Xw 0 2018-07-07 22:09:11 0 KU_O5udG6zpxOg-VcAEodg 3.0 If you decide to eat here, just be aware it is going to take about 2 hours from beginning to end. We have tried it multiple times, because I want to like it! I have been to it's other locations in NJ and never had a bad experience. 

The food is good, but it takes a very long time to come out. The waitstaff is very young, but usually pleasant. We have just had too many experiences where we spent way too long waiting. We usually opt for another diner or restaurant on the weekends, in order to be done quicker. 0 mh_-eMZ6K5RLWhZyISBhwA NEUTRAL If you decide to eat here, just be aware it is going to take about 2 hours from beginning to end. We have tried it multiple times, because I want to like it! I have been to it's other locations in NJ and never had a bad experience. The food is good, but it takes a very long time to come out. The waitstaff is very young, but usually pleasant. We have just had too many experiences where we spent way too long waiting. We usually opt for another diner or restaurant on the weekends, in order to be done quicker. 7ATYjTIgM3jUlt4UM3IypQ 1 2012-01-03 15:28:18 0 BiTunyQ73aT9WBnpR9DZGw 5.0 I've taken a lot of spin classes over the years, and nothing compares to the classes at Body Cycle. From the nice, clean space and amazing bikes, to the welcoming and motivating instructors, every class is a top notch work out.

For anyone who struggles to fit workouts in, the online scheduling system makes it easy to plan ahead (and there's no need to line up way in advanced like many gyms make you do).

There is no way I can write this review without giving Russell, the owner of Body Cycle, a shout out. Russell's passion for fitness and cycling is so evident, as is his desire for all of his clients to succeed. He is always dropping in to classes to check in/provide encouragement, and is open to ideas and recommendations from anyone. Russell always wears a smile on his face, even when he's kicking your butt in class! 1 OyoGAe7OKpv6SyGZT5g77Q POSITIVE I've taken a lot of spin classes over the years, and nothing compares to the classes at Body Cycle. From the nice, clean space and amazing bikes, to the welcoming and motivating instructors, every class is a top notch work out. For anyone who struggles to fit workouts in, the online scheduling system makes it easy to plan ahead and there's no need to line up way in advanced like many gyms make you do . There is no way I can write this review without giving Russell, the owner of Body Cycle, a shout out. Russell's passion for fitness and cycling is so evident, as is his desire for all of his clients to succeed. He is always dropping in to classes to check in provide encouragement, and is open to ideas and recommendations from anyone. Russell always wears a smile on his face, even when he's kicking your butt in class! YjUWPpI6HXG530lwP-fb2A 0 2014-02-05 20:30:30 0 saUsX_uimxRlCVr67Z4Jig 3.0 Family diner. Had the buffet. Eclectic assortment: a large chicken leg, fried jalapeño, tamale, two rolled grape leaves, fresh melon. All good. Lots of Mexican choices there. Also has a menu with breakfast served all day long. Friendly, attentive staff. Good place for a casual relaxed meal with no expectations. Next to the Clarion Hotel. 0 8g_iMtfSiwikVnbP2etR0A NEUTRAL Family diner. Had the buffet. Eclectic assortment a large chicken leg, fried jalape o, tamale, two rolled grape leaves, fresh melon. All good. Lots of Mexican choices there. Also has a menu with breakfast served all day long. Friendly, attentive staff. Good place for a casual relaxed meal with no expectations. Next to the Clarion Hotel. kxX2SOes4o-D3ZQBkiMRfA 1 2015-01-04 00:01:03 0 AqPFMleE6RsU23_auESxiA 5.0 Wow! Yummy, different, delicious. Our favorite is the lamb curry and korma. With 10 different kinds of naan!!! Don't let the outside deter you

For Sentiment Analysis

In [0]:
# Convert to pandas for external model processing
pdf = df.limit(1000).orderBy("date")
pdf = pdf.toPandas()
pdf.display()

business_id cool date funny review_id stars text useful user_id sentiment_based_on_stars clean_text xJ3NSwE0xhdtA-tB_y_rNQ 0 2005-05-11 13:51:10 0 RcsyeHfZqpGdb9z-AkUdSA 3.0 Lots and lots of mostly fried seafood. Surprisingly expensive for a working class joint. It's the kind of place a dock worker would take his family for a fancy meal and not feel out of place. And it's definitely a New Orleans sort of experience. But the food isn't that great. 4 iUeZhkI0OK0BisakOkb3pQ NEUTRAL Lots and lots of mostly fried seafood. Surprisingly expensive for a working class joint. It's the kind of place a dock worker would take his family for a fancy meal and not feel out of place. And it's definitely a New Orleans sort of experience. But the food isn't that great. PY9GRfzr4nTZeINf346QOw 0 2005-05-15 00:39:29 0 JFjQ5RntPGhsNO2agAEYtg 5.0 Best casino in Reno. 4 deck and 2 deck blackjack, real drink glasses (no plastic fratboy cups), amazing decorum that will burn your retinas, and the restaurants inside are better the big casinos on the strip by a factor of a thousand.
The rooms are stellar for the price. Get a hot tub and chilllllll. 0 c8qFkI_VusWo0xZvkjfBWQ POSITIVE Best casino in Reno. 4 deck and 2 deck blackjack, real drink glasses no plastic fratboy cups , amazing decorum that will burn your retinas, and the restaurants inside are better the big casinos on the strip by a factor of a thousand. The rooms are stellar for the price. Get a hot tub and chilllllll. 0ZETsmrLSGWaBu1NNdcmYw 0 2005-05-18 15:44:55 0 9eeoAUQEJDw0KYV5NPYH-A 2.0 Good luck finding anyone to help you. Poor poor customer service. 2 -qoyKSF2G3PkR_7XNoJfpQ NEGATIVE Good luck finding anyone to help you. Poor poor customer service. 2S_CEQYBbp8RO1bJm_1mng 4 2005-07-10 17:20:44 3 ep8FfviAfqHNyhpW6MQ2jA 2.0 Hipsters unite! I've never had a good time at The Taint, despite several people's attempts top tell me otherwise. I'm not impressed by the apathy here, or the dirty-headed Garden District crapfest of regular clientele. Boo. 3 n-lBS02-3yvlY5Q91mmwDA NEGATIVE Hipsters unite! I've never had a good time at The Taint, despite several people's attempts top tell me otherwise. I'm not impressed by the apathy here, or the dirty headed Garden District crapfest of regular clientele. Boo. htO_nlxkEsYHzDrtbiUxew 0 2006-05-02 22:18:26 0 i_fJQ_-9S9qhH2hl5bMIiw 3.0 i was looking forward to a new coffee spot, but this won't be it for me. they dont have a menu first off, and im not a coffee connoisseur, so i was a little thrown off. i kept it simple, asked for an iced tea, but they did give me hot tea w/a cup of ice. v. artsy crowd here, great for people watching, but not for studying. its a little loud, my headphones were not enough to block out the noise, so i was stuck listening to watever they chose, which wasn't my preference. the servers were all really nice, and they kept cleaning the tables quite often. all in all it wasnt a bad experience, but not one to keep me coming back either... 3 FBRjdSizGuMyxQuSSwzarg NEUTRAL i was looking forward to a new coffee spot, but this won't be it for me. they dont have a menu first off, and im not a coffee connoisseur, so i was a little thrown off. i kept it simple, asked for an iced tea, but they did give me hot tea w a cup of ice. v. artsy crowd here, great for people watching, but not for studying. its a little loud, my headphones were not enough to block out the noise, so i was stuck listening to watever they chose, which wasn't my preference. the servers were all really nice, and they kept cleaning the tables quite often. all in all it wasnt a bad experience, but not one to keep me coming back either... 6jgRI0lDt48CY8j1GAGuKQ 1 2007-05-17 20:41:04 1 KAD7AekVYfOAFzQnuy-rAg 5.0 these people are great.
through the years we've experienced everything and seen probably every doctor. these are true animal people, through and through, and you can always count on them for the best. not much else to say! 5 X5EAMkKCHTpmso9ILIFRUg POSITIVE these people are 

# Generative AI for Sentiment (LLMs like Gemini, ChatGPT): Google Gemini LLM
- basic sentiment classify
- summary of reviews in each sentiment catogory

In [0]:
import google.generativeai as genai

import pandas as pd

def gemini(review_file):
    gemini_api = "YOUR_API_KEY" # Please enter the API key here
    client = genai.configure(api_key=gemini_api)
    if review_file is None:
        return "No file uploaded."
    #read json file and organize review for prompt
    #df = review_file.toPandas()
    df = review_file
    df = df[["clean_text", "date","sentiment_based_on_stars","review_id", "stars"]]
    df["number"] = ["review "+str(i) for i in range(1,df.shape[0]+1)]
    df["for_prompt"] = df[["number","clean_text"]].apply(lambda x:": ".join(x.values.astype(str)),axis=1)
    summary_container = []
    #50 rows per run
    result_df = pd.DataFrame(columns=["review_id","review", "sentiment analysis","date","sentiment_based_on_stars"])
    row_count = 0

    while row_count < len(df):
      df_sub = df.iloc[row_count:row_count+30, :]
      text_to_topic = "\n".join(df_sub["for_prompt"])
      row_count += 30
      prompt = """
    In the following text, you will see a list of customer review.
    Can you (1) do sentiment analysis for each review and catogorize based on three categories: "positive","negative","neutral" (2) give me three summary reports, one is to summarize all reviews that are catogorized into "positive", one is to summarize all reviews that are catogorized into "negative", one is to summarize all reviews that are catogorized into "neutral".
    Respond strictly as a plain JSON array (do not include word "json" in the very top):
    {{ {{
        "summary reports for each sentiment catogory":{{"positive": "brief explanation", "negative":"brief explanation","neutral":"brief explanation"
    }},
      
    {{"review_analysis":{{{{
      "review 1": {{{{"sentiment analysis":"positive/negative/neutral"}}}},
      "...":{{{{...}}}}
      }}}}}}
    }}
    And here are all the review text: {text_to_topic}""".format(text_to_topic=text_to_topic)
      model = genai.GenerativeModel("gemini-2.0-flash")
      response = model.generate_content(prompt)
    

      import re
      import json

      json_str_match = re.search(r'\{.*\}', response.text, re.DOTALL)

      if json_str_match:
          json_str = json_str_match.group(0)

          topics_json_object = json.loads(f"[{json_str}]")

      review_summary = topics_json_object[0]["summary reports for each sentiment catogory"]
      summary_container.append(review_summary)

      review_analysis = topics_json_object[0]["review_analysis"]

      new_df = pd.DataFrame(review_analysis).transpose()
      new_df["review_id"] = df_sub["review_id"].values
      new_df["review"] = df_sub["clean_text"].values
      new_df["date"] = df_sub["date"].values
      new_df["sentiment_based_on_stars"] = df_sub["sentiment_based_on_stars"].values


      result_df = pd.concat([result_df,new_df],ignore_index=True)
      columns_to_keep = ["review_id", "review", "sentiment analysis", "date", "sentiment_based_on_stars"]
      pandas_df = result_df[columns_to_keep]
      result = spark.createDataFrame(pandas_df)
  #sentiment summary part

    prompt2 = """
    In the following text, you will see a list of customer review's sentiment summary.
    Can you (1) summarize the content within each sentiment category from "positive","negative","neutral". 
    Respond strictly as a plain JSON array (do not include word "json" in the very top):
    {{ {{
        "summary reports for each sentiment catogory":{{"positive": "brief explanation", "negative":"brief explanation","neutral":"brief explanation"
    }}
    }}
    And here are all the customer review's sentiment summary: {text_to_topic}""".format(text_to_topic= f"{summary_container}")
    response_summary = model.generate_content(prompt2)
    json_str_match = re.search(r'\{.*\}', response_summary.text, re.DOTALL)

    if json_str_match:
      json_str = json_str_match.group(0)

      topics_json_object = json.loads(f"[{json_str}]")

      review_summary = topics_json_object[0]["summary reports for each sentiment catogory"]
      sentiment_summary = pd.DataFrame([review_summary]).transpose()
      

    return result, sentiment_summary


In [0]:
# Running Google Gemini LLM
gemini_result, summary = gemini(pdf)

/root/.ipykernel/1397/command-1326052748810717-4267752854:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["number"] = ["review "+str(i) for i in range(1,df.shape[0]+1)]
/root/.ipykernel/1397/command-1326052748810717-4267752854:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["for_prompt"] = df[["number","clean_text"]].apply(lambda x:": ".join(x.values.astype(str)),axis=1)


In [0]:
# Checking results for sentiment analysis
gemini_result.limit(5).display()

review_id review sentiment analysis date sentiment_based_on_stars RcsyeHfZqpGdb9z-AkUdSA Lots and lots of mostly fried seafood. Surprisingly expensive for a working class joint. It's the kind of place a dock worker would take his family for a fancy meal and not feel out of place. And it's definitely a New Orleans sort of experience. But the food isn't that great. negative 2005-05-11 13:51:10 NEUTRAL JFjQ5RntPGhsNO2agAEYtg Best casino in Reno. 4 deck and 2 deck blackjack, real drink glasses no plastic fratboy cups , amazing decorum that will burn your retinas, and the restaurants inside are better the big casinos on the strip by a factor of a thousand. The rooms are stellar for the price. Get a hot tub and chilllllll. positive 2005-05-15 00:39:29 POSITIVE 9eeoAUQEJDw0KYV5NPYH-A Good luck finding anyone to help you. Poor poor customer service. negative 2005-05-18 15:44:55 NEGATIVE ep8FfviAfqHNyhpW6MQ2jA Hipsters unite! I've never had a good time at The Taint, despite several people's attempts top tell me otherwise. I'm not impressed by the apathy here, or the dirty headed Garden District crapfest of regular clientele. Boo. negative 2005-07-10 17:20:44 NEGATIVE i_fJQ_-9S9qhH2hl5bMIiw i was looking forward to a new coffee spot, but this won't be it for me. they dont have a menu first off, and im not a coffee connoisseur, so i was a little thrown off. i kept it simple, asked for an iced tea, but they did give me hot tea w a cup of ice. v. artsy crowd here, great for people watching, but not for studying. its a little loud, my headphones were not enough to block out the noise, so i was stuck listening to watever they chose, which wasn't my preference. the servers were all really nice, and they kept cleaning the tables quite often. all in all it wasnt a bad experience, but not one to keep me coming back either... neutral 2006-05-02 22:18:26 NEUTRAL

In [0]:
# Checking results for summary reports
summary.display()

0 Positive reviews consistently emphasize excellent food quality, friendly and efficient service, pleasant atmosphere, good value for money, and overall enjoyable experiences. Many highlight specific dishes or features, praising staff attentiveness, cleanliness, and a welcoming environment. Customers frequently express satisfaction, a willingness to return, and strong recommendations. Negative reviews frequently center on issues like poor food quality, slow or rude service, uncleanliness, high prices relative to quality, and disappointing experiences. Common complaints include long wait times, inattentive staff, incorrect orders, and negative interactions with staff. Dissatisfaction is often expressed with a reluctance to return. Neutral reviews tend to be balanced assessments, acknowledging both positive and negative aspects without strong emotional leaning. They often provide factual information about the establishment, such as its location, offerings, or atmosphere, without expressing strong sentiments. These reviews may describe a mixed experience or highlight specific details without clear favor or disfavor, often offering constructive feedback.

In [0]:
from sklearn.metrics import accuracy_score, f1_score
gemini_result = gemini_result.toPandas()
# Clean missing/null rows
gemini_result = gemini_result.dropna(subset=['sentiment_based_on_stars', 'sentiment analysis'])

# Normalize labels
true_labels = gemini_result['sentiment_based_on_stars'].str.lower()
predicted_labels = gemini_result['sentiment analysis'].str.lower()

# Compute scores
gemini_accuracy = accuracy_score(true_labels, predicted_labels)
gemini_f1 = f1_score(true_labels, predicted_labels, average='weighted')

# Output
print("Accuracy:", gemini_accuracy)
print("F1 Score:", gemini_f1)

Accuracy: 0.8804878048780488
F1 Score: 0.8747191989987608


# Traditional Pre-trained ML Models (Neural, But Not Generative): Azure sentiment analysis

In [0]:
import pandas as pd
def analyze_sentiment(df) -> None:
    #read the uploaded file
    if df is None:
        return "No data provided."

    #df = df.toPandas()
    df = df[["review_id","clean_text", "date","sentiment_based_on_stars"]]
    import os
    from azure.core.credentials import AzureKeyCredential
    from azure.ai.textanalytics import TextAnalyticsClient
  #Max 10 records are permitted.
    row_count = 0
    reviews = []
    sentiment_result = []
    while row_count < len(df):
      df_sub = df.iloc[row_count:row_count+10, :]
      row_count += 10
      #sentiment analysis
      API_KEY = "YOUR_API_KEY" # Please enter API key here
      end_point = "YOUR_ENDPOINT" # Please enter Endpoint here
      text_analytics_client = TextAnalyticsClient(endpoint=end_point,credential=AzureKeyCredential(API_KEY))
      documents = df_sub["clean_text"].tolist()
      result = text_analytics_client.analyze_sentiment(documents, show_opinion_mining=True)
      docs = [doc for doc in result if not doc.is_error]

      for idx, doc in enumerate(docs):
          reviews.append(documents[idx])
          sentiment_result.append(doc.sentiment)

    result_df = pd.DataFrame({"review_id":df["review_id"].to_list(),"review":reviews,"sentiment analysis": sentiment_result, "date": df["date"].tolist(), "sentiment_based_on_stars": df["sentiment_based_on_stars"].tolist()})
    return result_df

In [0]:
# Performing azure sentiment analysis
azure_result = analyze_sentiment(pdf)
azure_result.display()

review_id review sentiment analysis date sentiment_based_on_stars RcsyeHfZqpGdb9z-AkUdSA Lots and lots of mostly fried seafood. Surprisingly expensive for a working class joint. It's the kind of place a dock worker would take his family for a fancy meal and not feel out of place. And it's definitely a New Orleans sort of experience. But the food isn't that great. negative 2005-05-11 13:51:10 NEUTRAL JFjQ5RntPGhsNO2agAEYtg Best casino in Reno. 4 deck and 2 deck blackjack, real drink glasses no plastic fratboy cups , amazing decorum that will burn your retinas, and the restaurants inside are better the big casinos on the strip by a factor of a thousand. The rooms are stellar for the price. Get a hot tub and chilllllll. positive 2005-05-15 00:39:29 POSITIVE 9eeoAUQEJDw0KYV5NPYH-A Good luck finding anyone to help you. Poor poor customer service. mixed 2005-05-18 15:44:55 NEGATIVE ep8FfviAfqHNyhpW6MQ2jA Hipsters unite! I've never had a good time at The Taint, despite several people's attempts top tell me otherwise. I'm not impressed by the apathy here, or the dirty headed Garden District crapfest of regular clientele. Boo. negative 2005-07-10 17:20:44 NEGATIVE i_fJQ_-9S9qhH2hl5bMIiw i was looking forward to a new coffee spot, but this won't be it for me. they dont have a menu first off, and im not a coffee connoisseur, so i was a little thrown off. i kept it simple, asked for an iced tea, but they did give me hot tea w a cup of ice. v. artsy crowd here, great for people watching, but not for studying. its a little loud, my headphones were not enough to block out the noise, so i was stuck listening to watever they chose, which wasn't my preference. the servers were all really nice, and they kept cleaning the tables quite often. all in all it wasnt a bad experience, but not one to keep me coming back either... mixed 2006-05-02 22:18:26 NEUTRAL KAD7AekVYfOAFzQnuy-rAg these people are great. through the years we've experienced everything and seen probably every doctor. these are true animal people, through and through, and you can always count on them for the best. not much else to say! positive 2007-05-17 20:41:04 POSITIVE NbT7iIVr8rz6tglE7tYTAg Located right at the Union Station Metro stop walking distance to all of downtown but metro able too , this place was a good deal on the weekend. Prices spike during the week when business peeps fly in and their companies are paying the bill. The room was clean, the bed was super comfy with TONS of pillows one sure way to my heart . The bathroom was large with a tub and too many white towels for two people. Subtracted one star cause the coffee machine in our room sucked and the door was thin so you could hear people children in the hall at WAY too early in the morning. The main lobby is really a cool place tho. Definitely worth checking out if you're in the area. mixed 2007-05-23 08:03:29 POSITIVE ssMrjqKRJxH-Rag5pPT5oQ A great lunch or dinner stop in Reno, NV. We've had some fine meals in this establishment......Tyler manager does a great job with his staff, and it shows in the overall results. They are also a pub, so its got a great selection of beers and wines too! positive 2007-12-08 19:17:57 POSITIVE y1CYqccQLsn8GGXYS4q6tQ They served me a frozen pizza and skunked beer. 'Nuff said. neutral 2008-04-30 14:54:01 NEGATIVE Pgh9POx-bH7JFggKXqXWMQ As far as I know, this is the best video rental store in existence. The staff is knowledgeable and friendly, but the selection really sets it apart. Suppose you want to rent the newest release and a VHS of the best hockey fights of the 1970s...They would probably have both available at a very low cost. I only wish that there was a place like Casa Video in Chicago. positive 2008-04-30 15:49:16 POSITIVE yqQmwEhvkAySMyGrRsRjQw Ick. That sums up my experience at Dinardo's in one word. Dinardo's gave me that Ick vibe the minute I set my foot in the door. THough we were greeted by a very friendly hostess, the place looked like a run down diner on the interio

In [0]:
# Checking Performance of Azure Sentiment Analysis
from sklearn.metrics import accuracy_score, f1_score
true_labels = azure_result['sentiment_based_on_stars'].str.lower()
predicted_labels = azure_result['sentiment analysis']
azure_accuracy  = accuracy_score(true_labels, predicted_labels)
azure_f1 = f1_score(true_labels, predicted_labels, average='weighted')
print("Accuracy:", accuracy_score(true_labels, predicted_labels))
print("F1 Score:", f1_score(true_labels, predicted_labels, average='weighted'))

Accuracy: 0.468
F1 Score: 0.5908392701637984


# Traditional Pre-trained ML Models (Neural, But Not Generative): DistilBERT base uncased finetuned SST-2 from Hugging Face

In [0]:
# Imports
import torch
from transformers import pipeline
import pandas as pd
from tqdm.auto import tqdm  # Progress bar

In [0]:
# Initialize model and tokenizer explicitly
model_name = "distilbert-base-uncased-finetuned-sst-2-english"

hf_pipeline = pipeline(
    "sentiment-analysis",
    model=model_name,
    tokenizer=model_name,
    device=0 if torch.cuda.is_available() else -1,
    truncation=True
)

config.json:   0%|          | 0.00/629 [00:00<?, ?B/s]

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


model.safetensors:   0%|          | 0.00/268M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

Device set to use cpu


In [0]:
def batch_sentiment_analysis(text_list, batch_size=32):
    results = []
    for i in tqdm(range(0, len(text_list), batch_size)):
        batch = text_list[i:i + batch_size]
        # Truncate texts manually before passing (extra safety)
        batch = [text[:2000] for text in batch]  
        preds = hf_pipeline(batch)
        batch_results = [pred['label'] for pred in preds]
        results.extend(batch_results)
    return results

In [0]:
# Convert to pandas
# pdf_pd = pdf.toPandas()
pdf_hf = pdf
texts = pdf_hf["clean_text"].tolist()

# Run batch sentiment analysis
pdf_hf["huggingface_sentiment"] = batch_sentiment_analysis(texts, batch_size=32)

# If you want to use Spark again:
pdf_hf = spark.createDataFrame(pdf_hf)
pdf_hf.display()

  0%|          | 0/32 [00:00<?, ?it/s]

business_id cool date funny review_id stars text useful user_id sentiment_based_on_stars clean_text huggingface_sentiment xJ3NSwE0xhdtA-tB_y_rNQ 0 2005-05-11 13:51:10 0 RcsyeHfZqpGdb9z-AkUdSA 3.0 Lots and lots of mostly fried seafood. Surprisingly expensive for a working class joint. It's the kind of place a dock worker would take his family for a fancy meal and not feel out of place. And it's definitely a New Orleans sort of experience. But the food isn't that great. 4 iUeZhkI0OK0BisakOkb3pQ NEUTRAL Lots and lots of mostly fried seafood. Surprisingly expensive for a working class joint. It's the kind of place a dock worker would take his family for a fancy meal and not feel out of place. And it's definitely a New Orleans sort of experience. But the food isn't that great. NEGATIVE PY9GRfzr4nTZeINf346QOw 0 2005-05-15 00:39:29 0 JFjQ5RntPGhsNO2agAEYtg 5.0 Best casino in Reno. 4 deck and 2 deck blackjack, real drink glasses (no plastic fratboy cups), amazing decorum that will burn your retinas, and the restaurants inside are better the big casinos on the strip by a factor of a thousand.
The rooms are stellar for the price. Get a hot tub and chilllllll. 0 c8qFkI_VusWo0xZvkjfBWQ POSITIVE Best casino in Reno. 4 deck and 2 deck blackjack, real drink glasses no plastic fratboy cups , amazing decorum that will burn your retinas, and the restaurants inside are better the big casinos on the strip by a factor of a thousand. The rooms are stellar for the price. Get a hot tub and chilllllll. POSITIVE 0ZETsmrLSGWaBu1NNdcmYw 0 2005-05-18 15:44:55 0 9eeoAUQEJDw0KYV5NPYH-A 2.0 Good luck finding anyone to help you. Poor poor customer service. 2 -qoyKSF2G3PkR_7XNoJfpQ NEGATIVE Good luck finding anyone to help you. Poor poor customer service. NEGATIVE 2S_CEQYBbp8RO1bJm_1mng 4 2005-07-10 17:20:44 3 ep8FfviAfqHNyhpW6MQ2jA 2.0 Hipsters unite! I've never had a good time at The Taint, despite several people's attempts top tell me otherwise. I'm not impressed by the apathy here, or the dirty-headed Garden District crapfest of regular clientele. Boo. 3 n-lBS02-3yvlY5Q91mmwDA NEGATIVE Hipsters unite! I've never had a good time at The Taint, despite several people's attempts top tell me otherwise. I'm not impressed by the apathy here, or the dirty headed Garden District crapfest of regular clientele. Boo. NEGATIVE htO_nlxkEsYHzDrtbiUxew 0 2006-05-02 22:18:26 0 i_fJQ_-9S9qhH2hl5bMIiw 3.0 i was looking forward to a new coffee spot, but this won't be it for me. they dont have a menu first off, and im not a coffee connoisseur, so i was a little thrown off. i kept it simple, asked for an iced tea, but they did give me hot tea w/a cup of ice. v. artsy crowd here, great for people watching, but not for studying. its a little loud, my headphones were not enough to block out the noise, so i was stuck listening to watever they chose, which wasn't my preference. the servers were all really nice, and they kept cleaning the tables quite often. all in all it wasnt a bad experience, but not one to keep me coming back either... 3 FBRjdSizGuMyxQuSSwzarg NEUTRAL i was looking forward to a new coffee spot, but this won't be it for me. they dont have a menu first off, and im not a coffee connoisseur, so i was a little thrown off. i kept it simple, asked for an iced tea, but they did give me hot tea w a cup of ice. v. artsy crowd here, great for people watching, but not for studying. its a little loud, my headphones were not enough to block out the noise, so i was stuck listening to watever they chose, which wasn't my preference. the servers were all really nice, and they kept cleaning the tables quite often. all in all it wasnt a bad experience, but not one to keep me coming back either... NEGATIVE 6jgRI0lDt48CY8j1GAGuKQ 1 2007-05-17 20:41:04 1 KAD7AekVYfOAFzQnuy-rAg 5.0 these people are great.
through the years we've experienced everything and seen probably every doctor. these are true animal people, through and through, and you can always count on them for the best. not mu

In [0]:
pdf_hf = pdf_hf.toPandas()

In [0]:
# Checking Performance of Hugging Face Sentiment Analysis
from sklearn.metrics import accuracy_score, f1_score
true_labels = pdf_hf["sentiment_based_on_stars"]
predicted_labels = pdf_hf["huggingface_sentiment"]
hf_accuracy  = accuracy_score(true_labels, predicted_labels)
hf_f1 = f1_score(true_labels, predicted_labels, average='weighted')
print("Accuracy:", hf_accuracy)
print("F1 Score:",hf_f1)

Accuracy: 0.832
F1 Score: 0.7790501723858956


# Traditional Sentiment Analysis (Non-Neural, Rule/Stat-Based): 
- VADER: Lexicon + heuristics (for social media, emojis, punctuation, negation)
- TextBlob: Based on Pattern's NB classifier, gives polarity + subjectivity

VADER 
- has a dictionary of ~7,500 words, each assigned a sentiment score between -4 (most negative) and +4 (most positive).

- Returns 4 scores: 'neg', 'neu', 'pos', and compound (overall score from -1 to +1)

In [0]:
from nltk.sentiment import SentimentIntensityAnalyzer
import nltk
import pandas as pd
nltk.download('vader_lexicon')
def vader (df):
  #read the uploaded file
    if df is None:
        return "No file uploaded."
    
    df = df[["review_id","clean_text", "date","sentiment_based_on_stars"]]

    sia = SentimentIntensityAnalyzer()
    df["vader_scores"] = df["clean_text"].apply(lambda x: sia.polarity_scores(x))
    df["vader_compound"] = df["vader_scores"].apply(lambda x: x["compound"])
    def get_sentiment_label(score):
      if score >= 0.5:
        return "positive"
      if score <= -0.5:
        return "negtive"
      else:
        return "neutral"
    df["vader_sentiment"] = df["vader_compound"].apply(get_sentiment_label)
    return df



[nltk_data] Downloading package vader_lexicon to /root/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


In [0]:
# Running Vader Sentiment Analysis
pdf_vd = pdf
vader_result = vader(pdf_vd)

/root/.ipykernel/1397/command-1326052748810738-2133329603:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["vader_scores"] = df["clean_text"].apply(lambda x: sia.polarity_scores(x))
/root/.ipykernel/1397/command-1326052748810738-2133329603:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["vader_compound"] = df["vader_scores"].apply(lambda x: x["compound"])
/root/.ipykernel/1397/command-1326052748810738-2133329603:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Da

In [0]:
vader_result.head(5)

review_id  ... vader_sentiment
0  RcsyeHfZqpGdb9z-AkUdSA  ...         neutral
1  JFjQ5RntPGhsNO2agAEYtg  ...        positive
2  9eeoAUQEJDw0KYV5NPYH-A  ...         neutral
3  ep8FfviAfqHNyhpW6MQ2jA  ...         negtive
4  i_fJQ_-9S9qhH2hl5bMIiw  ...        positive

[5 rows x 7 columns]

In [0]:
# Checking Performance of Vader Sentiment Library
from sklearn.metrics import accuracy_score, f1_score
true_labels = vader_result['sentiment_based_on_stars'].str.lower()
predicted_labels = vader_result["vader_sentiment"]
vader_accuracy  = accuracy_score(true_labels, predicted_labels)
vader_f1 = f1_score(true_labels, predicted_labels, average='weighted')
print("Accuracy:", vader_accuracy)
print("F1 Score:", vader_f1)

Accuracy: 0.669
F1 Score: 0.617362021075971


Combining the output of all the models and exporting to blob storage

In [0]:
# Combining the results from all the different models
gemini_result.rename(columns={'sentiment analysis':'gemini_sentiment'}, inplace=True)
azure_result.rename(columns={'sentiment analysis':'azure_sentiment'}, inplace=True)

sentiment_result = gemini_result \
    .merge(pdf_hf[['review_id', 'huggingface_sentiment']], on='review_id', how='left') \
        .merge(vader_result[['review_id', 'vader_sentiment']], on='review_id', how='left') \
            .merge(azure_result[['review_id', 'azure_sentiment']], on='review_id', how='left')

cols_to_upper = ['gemini_sentiment','huggingface_sentiment', 'vader_sentiment', 'azure_sentiment','sentiment_based_on_stars']
sentiment_result[cols_to_upper] = sentiment_result[cols_to_upper].apply(lambda x: x.str.upper())

sentiment_result.head(5)

review_id  ... azure_sentiment
0  RcsyeHfZqpGdb9z-AkUdSA  ...        NEGATIVE
1  JFjQ5RntPGhsNO2agAEYtg  ...        POSITIVE
2  9eeoAUQEJDw0KYV5NPYH-A  ...           MIXED
3  ep8FfviAfqHNyhpW6MQ2jA  ...        NEGATIVE
4  i_fJQ_-9S9qhH2hl5bMIiw  ...           MIXED

[5 rows x 8 columns]

In [0]:
# Exporting the data to Azure Blob Storage
sentiment_result.to_csv("/dbfs/mnt/yelp/sentiment_result.csv", index=False)
summary.to_csv("/dbfs/mnt/yelp/gemini_sentiment_summary.csv", index=False)

In [0]:
%fs ls /mnt/yelp

path name size modificationTime dbfs:/mnt/yelp/gemini_sentiment_summary.csv gemini_sentiment_summary.csv 1175 1745185978000 dbfs:/mnt/yelp/sentiment_result.csv sentiment_result.csv 548191 1745185978000 dbfs:/mnt/yelp/yelp_academic_dataset_review.json yelp_academic_dataset_review.json 5341868833 1745106841000